In [1]:
import os
HOME = os.getcwd()
print('HOME: ',HOME)

import time
import math
import json
import random
import pandas as pd
import sys
import lxml
import sklearn as sk
import numpy as np

from sklearn.manifold import TSNE
from sklearn.cluster import KMeans
from sklearn.cluster import HDBSCAN, DBSCAN
from scipy.spatial.distance import cosine
from sklearn.metrics.pairwise import cosine_similarity

import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
import plotly.graph_objects as go

from scipy.sparse import csr_matrix, issparse, lil_matrix, coo_matrix

from tqdm import tqdm
from pandarallel import pandarallel

from numba import njit, prange, jit
from numba_progress import ProgressBar

import networkx as nx

HOME:  /Users/ericsuardi/Desktop/DataMiningProject23-24


In [48]:
# STANDARD_FILE = 'standard_small_order_printClustroids.json'
# ACTUAL_FILE = 'actual_small_order_printClustroids.json'

# STANDARD_FILE = 'standard_small.json'
# ACTUAL_FILE = 'actual_small.json'

STANDARD_FILE = 'standard_medium_last.json'
ACTUAL_FILE = 'actual_medium_last.json'

# STANDARD_FILE = 'standard_big_new_3.json'
# ACTUAL_FILE = 'actual_big_new_3.json'

K_SHINGLES = 3

In [49]:
# load standard and actual data
print("\nReading standard data...")
with open(os.path.join('data',STANDARD_FILE)) as f:
    standard = json.load(f)

print("\nReading actual data...")
with open(os.path.join('data', ACTUAL_FILE)) as f:
    actual = json.load(f)

# load the data into a dataframe
print("\nCreating standard dataframe...")
dfStandard = pd.DataFrame(standard)
print("\nCreating actual dataframe...")
dfActual = pd.DataFrame(actual)

# print head of the dataframes
print(dfStandard.head())
print(dfActual.head())

# get the unique cities and items of the standard data
cities = []
items = []
longestRoute = 0
shortestRoute = np.inf
maxItemQuantity = 0

standardRefIds = []
for index, s in dfStandard.iterrows():
    #print(s)
    idS = s['id']
    route = s['route']
    standardRefIds.append(int(idS[1]))
    for trip in route:
        cities.append(trip['from']) 
        items.extend(trip['merchandise'].keys())
        maxItemQuantity = max(maxItemQuantity, max(trip['merchandise'].values()))
    if len(route) > 0:
        cities.append(route[-1]['to'])
        
    if len(route) > longestRoute:
        longestRoute = len(route)
        
    if len(route) < shortestRoute:
        shortestRoute = len(route)
print("\nFinished preparing standard data")

actualRefStandardIds = []
for index, s in dfActual.iterrows():
    #print(s)
    idS = s['id']
    route = s['route']
    idStandard = s['sroute']
    actualRefStandardIds.append(int(idStandard[1]))
    for trip in route:
        cities.append(trip['from'])
        items.extend(trip['merchandise'].keys())
        maxItemQuantity = max(maxItemQuantity, max(trip['merchandise'].values()))
        
    if len(route) > 0:
        cities.append(route[-1]['to'])
        
    if len(route) > longestRoute:
        longestRoute = len(route)
    
    if len(route) < shortestRoute:
        shortestRoute = len(route)
print("\nFinished preparing actual data")


# find the unique cities and items
uniqueCities = sorted(list(set(cities)))
#uniqueCities.insert(0, 'NULL')          # add NULL city, for padding vectors with different lengths (trips in routes)
uniqueItems = sorted(list(set(items)))

print("\nSorted cities and items")

if shortestRoute < 2:
    K_SHINGLES = 2

threeShingles = []

for i, c1 in enumerate(uniqueCities):
    for j, c2 in enumerate(uniqueCities):
        if i == j:
            continue
        for k, c3 in enumerate(uniqueCities):
            if j == k or i == k:
                continue
            threeShingles.append([c1, c2, c3])
            
permutations = math.perm(len(uniqueCities), K_SHINGLES)

print("\nComputed all possible three-shingles")

print("\nUnique cities: ", uniqueCities)
print("Unique items: ", uniqueItems)

print("\nNumber of cities: ", len(uniqueCities))
print("Number of items: ", len(uniqueItems))

print("\nLongest route: ", longestRoute)
print("Shortest route: ", shortestRoute)

print("\nMax item quantity: ", maxItemQuantity)

print("\nNumber of three-shingles: ", len(threeShingles))

print(f"\n{K_SHINGLES}-shingles: ", math.perm(len(uniqueCities), K_SHINGLES))
print(f"{K_SHINGLES}-shingles: ", math.comb(len(uniqueCities), K_SHINGLES))

print(f"\n\033[92mK-Shingles used: {K_SHINGLES} \033[0m")



Reading standard data...

Reading actual data...

Creating standard dataframe...

Creating actual dataframe...
   id                                              route
0  s0  [{'from': 'L’Aquila', 'to': 'Reggio Calabria',...
1  s1  [{'from': 'Trento', 'to': 'Fano', 'merchandise...
2  s2  [{'from': 'Foligno', 'to': 'Siena', 'merchandi...
3  s3  [{'from': 'Pozzuoli', 'to': 'Marano di Napoli'...
4  s4  [{'from': 'Vigevano', 'to': 'Piacenza', 'merch...
   id driver sroute                                              route
0  a0    J_3     s0  [{'from': 'L’Aquila', 'to': 'Aprilia', 'mercha...
1  a1    N_2     s0  [{'from': 'L’Aquila', 'to': 'Crotone', 'mercha...
2  a2    K_0     s0  [{'from': 'L’Aquila', 'to': 'Reggio Calabria',...
3  a3    T_3     s0  [{'from': 'L’Aquila', 'to': 'Aprilia', 'mercha...
4  a4    N_2     s0  [{'from': 'L’Aquila', 'to': 'Reggio Calabria',...

Finished preparing standard data

Finished preparing actual data

Sorted cities and items

Computed all possible three-

In [50]:
def hashShingles(shingles, n):
    # hash shingles
    string = "" 
    for shingle in shingles:
        string += str(shingle) + "," # [45, 4, 8] -> "45,4,8,"
    
    return hash(string) #% n

def createShingles(df, k, uniqueCities, uniqueItems, longestRoute, maxItemQuantity, permutations):
    # create shingles for each route
    shingles = []
    for index, s in df.iterrows():
        idS = s['id']
        route = s['route']
        shingle = [index]
        citiesInRoute = [] # napoli roma milano teramo bergamo [10,4,5,48,12] [10,4,5] [4,5,48] [5,48,12]
        merchandiseInRoute = np.zeros(len(uniqueItems))
        for trip in route:
            citiesInRoute.append(uniqueCities.index(trip['from']))
            #merchandiseInRoute += np.array(list(trip['merchandise'].values()))
            for item, n in trip['merchandise'].items():
                merchandiseInRoute[uniqueItems.index(item)] += n
        if len(route) > 0:
            citiesInRoute.append(uniqueCities.index(route[-1]['to']))
        if len(route) > 0:
            merchandiseInRoute = merchandiseInRoute / (maxItemQuantity*len(route))
        
        hashedShingles = []
        for i in range(len(citiesInRoute)-k+1):
            # Q: is it correct to set the modulo for the hash function to the number of permutations?
            # A: yes, because we want to have a unique hash for each shingle
            # Q: would it be better to use a different hash function?
            # A: yes, because the modulo function is not a good hash function
            hashedShingles.append(hashShingles(citiesInRoute[i:i+k], permutations) )
        
        shingle.append(np.array(hashedShingles))
        
        shingle.append(merchandiseInRoute) # quantity hot encoding
        
        shingles.append(shingle)
        
    return shingles # [ index, [shingles], [merchandise] ]

def create_shingles(s, k, uniqueCities, uniqueItems, longestRoute, maxItemQuantity, permutations):
    idS = s['id']
    route = s['route']
    shingle = [s.name]
    citiesInRoute = [] 
    merchandiseInRoute = np.zeros(len(uniqueItems))
    for trip in route:
        citiesInRoute.append(uniqueCities.index(trip['from']))
        for item, n in trip['merchandise'].items():
            merchandiseInRoute[uniqueItems.index(item)] += n
    if len(route) > 0:
        citiesInRoute.append(uniqueCities.index(route[-1]['to']))
    if len(route) > 0:
        merchandiseInRoute = merchandiseInRoute / (maxItemQuantity*len(route))
    
    hashedShingles = []
    for i in range(len(citiesInRoute)-k+1):
        hashedShingles.append(hashShingles(citiesInRoute[i:i+k], permutations))
    
    shingle.append(np.array(hashedShingles))
    shingle.append(merchandiseInRoute)
    
    return shingle

In [51]:
#standardSets = createShingles(dfStandard, k=K_SHINGLES, uniqueCities=uniqueCities, uniqueItems=uniqueItems, longestRoute=longestRoute, maxItemQuantity=maxItemQuantity, permutations=permutations)
#actualSets = createShingles(dfActual, k=K_SHINGLES, uniqueCities=uniqueCities, uniqueItems=uniqueItems, longestRoute=longestRoute, maxItemQuantity=maxItemQuantity, permutations=permutations)
pandarallel.initialize(progress_bar=True)
standardSets = dfStandard.parallel_apply(lambda s: create_shingles(s, K_SHINGLES, uniqueCities, uniqueItems, longestRoute, maxItemQuantity, permutations), axis=1)
standardSets = standardSets.tolist()
actualSets = dfActual.parallel_apply(lambda s: create_shingles(s, K_SHINGLES, uniqueCities, uniqueItems, longestRoute, maxItemQuantity, permutations), axis=1)
actualSets = actualSets.tolist()

print("\nstandardSets", len(standardSets), "shape first element", standardSets[0][1].shape, standardSets[0])
print("\nactualSets", len(actualSets),  "shape first element", standardSets[0][1].shape, actualSets[0])

print("\nstandardSets:", len(standardSets))
print("actualSets:", len(actualSets))

assert len(standardSets[0]) == 3, "The length of the standard set is not equal to 3 (index, shingles, merchandise)"
assert len(standardSets[0][2]) == len(uniqueItems), "The length of the merchandise vector is not equal to the number of unique items"

INFO: Pandarallel will run on 10 workers.
INFO: Pandarallel will use standard multiprocessing data transfer (pipe) to transfer data between the main process and workers.



standardSets 10 shape first element (23,) [0, array([ 8932198899962043773,  4379326325032197448,  5368052130114781945,
       -3829757074993702579, -2360327709055798138,  6696293365384302154,
       -8428419245597937912, -5359948911914471194,  8706567539145608108,
         618469908174660461, -4552736405985543778, -2547532667917435072,
        -643850399003232187, -3733817479783870885, -2483134898595101624,
       -5980116947508007794,  2340688983291223783,  1508015101886949708,
       -4732200213771702376,  -449811487060395229,  7908454611238110120,
       -3665858341071598914,   162806568445439196]), array([0.30166667, 0.37375   , 0.21875   , 0.25083333, 0.3125    ,
       0.27083333, 0.28666667, 0.20916667, 0.15625   , 0.28583333,
       0.25166667, 0.21833333, 0.18125   , 0.27208333, 0.17333333,
       0.23416667, 0.24083333, 0.19166667, 0.21416667, 0.22583333])]

actualSets 10000 shape first element (23,) [0, array([ 6824886187585928930,  5368052130114781945, -3829757074993702579

## Clustering

In [70]:


def jaccard_similarity_matrix(matrix):
    if 1.0 - np.count_nonzero(matrix) / matrix.size > 0.5:
        print("matrix jaccard is sparse")
        
        matrixCSR = csr_matrix(matrix)
        intersection = np.dot(matrixCSR, matrixCSR.T)
        intersection = intersection.todense()
        print("intersection", intersection.shape, type(intersection))
        #print("intersection", intersection.toarray(), type(intersection.toarray()))
        row_sums = matrix.sum(axis=1)
        print("row_sums", row_sums.shape)
        union = row_sums[:, None] + row_sums - intersection
        print("union", union.shape)
        union = np.where(union == 0, 1, union)  # avoid division by zero
        print("union", union.shape)
        jaccard_similarity = intersection / union
        print("jaccard_similarity", jaccard_similarity.shape, type(jaccard_similarity))
    else:
        print("matrix jaccard is not sparse")
        
        intersection = np.dot(matrix, matrix.T)
        print("intersection", intersection.shape)
        #print("intersection", intersection.toarray(), type(intersection.toarray()))
        row_sums = matrix.sum(axis=1)
        print("row_sums", row_sums.shape)
        union = row_sums[:, None] + row_sums - intersection
        print("union", union.shape)
        union = np.where(union == 0, 1, union)
        jaccard_similarity = intersection / union
        print("jaccard_similarity", jaccard_similarity.shape)
    print("jaccard_similarity contains nan", np.isnan(jaccard_similarity).any())   
    return jaccard_similarity

def jaccard_similarity_minhash(matrix):
    similarity_matrix = np.full((matrix.shape[0], matrix.shape[0]), np.inf)
    num_permutations = matrix.shape[1]
    for i in tqdm(range(matrix.shape[0])):
        for j in range(i + 1, matrix.shape[0]):
            similarity_matrix[i, j] = np.count_nonzero(matrix[i, :] == matrix[j, :]) / num_permutations
            similarity_matrix[j, i] = similarity_matrix[i, j]
                    
    # Create a full symmetric matrix from the upper triangular part
    #similarity_matrix = np.triu(similarity_matrix) + np.triu(similarity_matrix, 1).T
    np.fill_diagonal(similarity_matrix, 1)
    print("similarity_matrix", similarity_matrix.shape, similarity_matrix[0])
    return similarity_matrix

# def minhash(matrix, permutations):
#     minhash_matrix = np.full((matrix.shape[0], permutations), np.inf)
#     coeff_range = permutations * 100
#     index_range = permutations * 100

#     # Generate the hash functions
#     hash_functions = [lambda x, a=a, b=b: (a * x + b) % matrix.shape[1] for a, b in zip(random.sample(range(coeff_range), permutations), random.sample(range(index_range), permutations))]
    
#     for i in tqdm(range(matrix.shape[0]), desc="minhashing", miniters=1000):
#         indices = np.where(matrix[i] == 1)[0]
#         for k in range(permutations):
#             hashed_indices = np.array([hash_functions[k](j) for j in indices])
#             #print("hashed_indices", hashed_indices.shape, hashed_indices)
#             minhash_matrix[i, k] = np.min(hashed_indices, initial=matrix.shape[1]+1)
    
#     return minhash_matrix

def hash_function_hash_code(num_of_hashes,n_col,next_prime):
  
    #coeffA = np.array(pick_random_coefficients(num_of_hashes,max_column_length)).reshape((num_of_hashes,1))
    #coeffB = np.array(pick_random_coefficients(num_of_hashes,max_column_length)).reshape((num_of_hashes,1))

    coeffA = np.array(random.sample(range(0,n_col*100),num_of_hashes)).reshape((num_of_hashes,1))
    coeffB = np.array(random.sample(range(0,n_col*100),num_of_hashes)).reshape((num_of_hashes,1))

    x = np.arange(n_col).reshape((1,n_col))

    hash_code = (np.matmul(coeffA,x) + coeffB) % next_prime # (num_of_hashes,n_col) so how each column index is permuted

    return hash_code

def minhash(u,num_of_hashes):
    (n_row, n_col) = u.shape
    next_prime = n_col
    hash_code = hash_function_hash_code(num_of_hashes,n_col,next_prime)

    signature_array = np.empty(shape = (n_row,num_of_hashes))

    #t2 = time.time()

    for row in tqdm(range(n_row), desc="minhashing"):
        #print("row", row)
        ones_index = np.where(u[row,:]==1)[0]
        #if len(ones_index) == 0:
        signature_array[row,:] = np.zeros((1,num_of_hashes))
            #continue
        corresponding_hashes = hash_code[:,ones_index]
        #print("ones_index", ones_index.shape, ones_index)
        #print("corresponding_hashes", corresponding_hashes.shape, corresponding_hashes)
        row_signature = np.amin(corresponding_hashes,axis=1).reshape((1,num_of_hashes))

        signature_array[row,:] = row_signature

    return signature_array

def find_band_and_row_values(columns, threshold):
    previous_b = 1
    previous_r = columns
    for b in range(1, columns + 1):
        if columns % b == 0:
            r = columns // b
            if (1 / b) ** (1 / r)  <= threshold:
                if np.abs((1 / previous_b) ** (1 / previous_r) - threshold) < np.abs((1 / b) ** (1 / r) - threshold):
                    return previous_b, previous_r
                return b, r
    return columns, 1

def lsh(minhash_matrix, thresh_user=0.2):
    # Initialize the signature matrix
    columns = minhash_matrix.shape[1]
    
    # Generate the hash functions
   # hash_functions = [lambda x, a=a, b=b: (a * x + b) % minhash_matrix.shape[1] for a, b in zip(random.sample(range(1000), bands), random.sample(range(1000), bands))]
    hash_function = lambda x: hash(",".join([str(x[i]) for i in range(len(x))]))
    
    # b = bands
    # r = columns//bands
    b, r = find_band_and_row_values(columns, thresh_user)
    # If columns is not divisible by bands
    if columns % b != 0:
        # Find the closest number that makes it divisible
        while columns % b != 0:
            b -= 1
        r = columns // b
    #bands = b
        
    print("final bands", b)
    signature_matrix = np.full((minhash_matrix.shape[0], b), np.inf)
    
    # if threshold is 0.8,
    threshold = (1 / b) ** (1 / r) 
    print("lsh threshold", threshold)
    
    # For each band
    print("Computing hash values of bands...")
    hash_values = np.apply_along_axis(lambda x: hash_function(x) % minhash_matrix.shape[0], 1, minhash_matrix.reshape(-1, r))
    # Reshape the hash values to match the signature matrix
    hash_values = hash_values.reshape(minhash_matrix.shape[0], b)
    # Update the signature matrix
    signature_matrix = hash_values
            
    # find candidate pairs
    print("Finding candidate pairs...")
    candidate_pairs = []
    for i in tqdm(range(signature_matrix.shape[0])):
        # Compute the similarity of the current row with all following rows
        similarities = np.sum(signature_matrix[i+1:, :] == signature_matrix[i, :], axis=1) / b
        # Find the indices of the rows that have a similarity greater than or equal to the threshold
        indices = np.nonzero(similarities >= threshold)[0]
        # Add the pairs to the candidate pairs
        candidate_pairs.extend((i, i+1+index) for index in indices)
    
    return np.array(candidate_pairs)

def lsh_two_matrices(minhash_matrix1, minhash_matrix2, thresh_user=0.2):
    # Initialize the signature matrix
    columns = minhash_matrix1.shape[1]
    
    # Generate the hash functions
    # hash_functions = [lambda x, a=a, b=b: (a * x + b) % minhash_matrix.shape[1] for a, b in zip(random.sample(range(1000), bands), random.sample(range(1000), bands))]
    hash_function = lambda x: hash(",".join([str(x[i]) for i in range(len(x))]))
    
    # b = bands
    # r = columns//bands
    b, r = find_band_and_row_values(columns, thresh_user)
    # If columns is not divisible by bands
    if columns % b != 0:
        # Find the closest number that makes it divisible
        while columns % b != 0:
            b -= 1
        r = columns // b
    #bands = b
        
    print("final bands", b)
    signature_matrix1 = np.full((minhash_matrix1.shape[0], b), np.inf)
    signature_matrix2 = np.full((minhash_matrix2.shape[0], b), np.inf)
    
    # if threshold is 0.8,
    threshold = (1 / b) ** (1 / r) 
    print("lsh threshold", threshold)
    
    # For each band
    print("Computing hash values of bands...")
    hash_values1 = np.apply_along_axis(lambda x: hash_function(x) % minhash_matrix1.shape[0], 1, minhash_matrix1.reshape(-1, r))
    hash_values2 = np.apply_along_axis(lambda x: hash_function(x) % minhash_matrix2.shape[0], 1, minhash_matrix2.reshape(-1, r))
    # Reshape the hash values to match the signature matrix
    hash_values1 = hash_values1.reshape(minhash_matrix1.shape[0], b)
    hash_values2 = hash_values2.reshape(minhash_matrix2.shape[0], b)
    # Update the signature matrix
    signature_matrix1 = hash_values1
    signature_matrix2 = hash_values2
            
    # find candidate pairs
    print("Finding candidate pairs...")
    candidate_pairs = np.empty((minhash_matrix1.shape[0], 2))
    for i in tqdm(range(signature_matrix1.shape[0])):
        # Compute the similarity of the current row with all following rows
        similarities = np.sum(signature_matrix2 == signature_matrix1[i, :], axis=1) / b
        # Find the indices of the rows that have a similarity greater than or equal to the threshold
        #indices = np.nonzero(similarities >= threshold)[0]
        indexMax = np.argmax(similarities)
        simMax = similarities[indexMax]
        # Add the pairs to the candidate pairs
        #candidate_pairs.extend((i, i+1+index) for index in indices)
        candidate_pairs[i] = [indexMax, simMax]
        
    return candidate_pairs
        

# def jaccard_similarity_minhash_lsh(matrix, bands=10):
#     #similarity_matrix = csr_matrix((matrix.shape[0], matrix.shape[0]), dtype=np.float64)
#     similarity_matrix = lil_matrix((matrix.shape[0], matrix.shape[0]), dtype=np.float64)
#     pairs = lsh(matrix, bands=bands, columns=matrix.shape[1])
#     uniqueRows = np.unique([i for i, j in pairs] + [j for i, j in pairs])
#     uniqueRowsSet = set([i for i, j in pairs] + [j for i, j in pairs])
#     print("uniqueRows numpy", len(uniqueRows))
#     print("uniqueRows set", len(uniqueRowsSet))
#     print("num of pairs", len(pairs))
#     print("num unique i", len(set([i for i, j in pairs])))
#     print("num unique j", len(set([j for i, j in pairs])))
#     print("num unique rows", len(uniqueRows))
#     map_i = {i: index for i, index in enumerate(uniqueRows)}
    
#     subset_matrix = matrix[list(uniqueRows)]
    
#     print("Computing jaccard similarity on subset matrix...")
#     print("subset matrix", subset_matrix.shape)
#     subset1 = subset_matrix[:, None, :]
#     subset2 = subset_matrix[None, :, :]
#     min_matrix = np.minimum(subset1, subset2) # (10, 100) -> (10, 1, 100) -> (1, 10, 100) -> (10, 10, 100)
#     sum_min_matrix = np.sum(min_matrix, axis=-1)
#     print("sum_min_matrix", sum_min_matrix.shape)
    
#     max_matrix = np.maximum(subset1, subset2)
#     sum_max_matrix = np.sum(max_matrix, axis=-1)
#     print("sum_max_matrix", sum_max_matrix.shape)
    
#     jaccard_similarity_matrix =  sum_min_matrix / sum_max_matrix
    
#     # map back to original matrix
#     print("Mapping back to original matrix...")
#     # for i, j in tqdm(pairs):
#     #     similarity_matrix[map_i[i], map_i[j]] = jaccard_similarity_matrix[i, j]
#     #     similarity_matrix[map_i[j], map_i[i]] = similarity_matrix[map_i[i], map_i[j]]
        
#     for i in tqdm(range(jaccard_similarity_matrix.shape[0])):
#         for j in range(i + 1, jaccard_similarity_matrix.shape[0]):
#             similarity_matrix[map_i[i], map_i[j]] = jaccard_similarity_matrix[i, j]
#             similarity_matrix[map_i[j], map_i[i]] = similarity_matrix[map_i[i], map_i[j]]
    
    
#     # for i, j in tqdm(pairs, desc="lsh sim"):
#     #     similarity_matrix[i, j] = np.count_nonzero(matrix[i, :] == matrix[j, :]) / matrix.shape[1]
#     #     similarity_matrix[j, i] = similarity_matrix[i, j]
    
#     similarity_matrix.setdiag(1)
    
#     return similarity_matrix

@njit(cache=True,)
def replicate_row(matrix, i):
    result = np.empty((matrix.shape[0], matrix.shape[1]))
    for j in range(matrix.shape[0]):
        result[j] = matrix[i]
    return result

@njit(cache=True, nogil=True, parallel=True)
def compute_subset_similarity_matrix(subset_matrix, progress_proxy):
    n = subset_matrix.shape[0]
    m = subset_matrix.shape[1]
    subset_matrix = subset_matrix.astype(np.int64)
    subset_similarity_matrix = np.zeros((n, n))
    subset2 = subset_matrix
    for i in prange(n):
        subset1 = subset_matrix[i].reshape(1, -1) #replicate_row(subset_matrix, i)    
        min_matrix = np.minimum(subset1, subset2)
        sum_min_matrix = np.sum(min_matrix, axis=-1)
        
        max_matrix = np.maximum(subset1, subset2)
        sum_max_matrix = np.sum(max_matrix, axis=-1)
        
        subset_similarity_matrix[i] = 1 - (np.divide(sum_min_matrix, sum_max_matrix)).T
        progress_proxy.update(1)
    return subset_similarity_matrix

@njit(cache=True, nogil=True, parallel=False)
def compute_subset_similarity_matrix_only_pairs(matrix, matrixMerch, pairs, progress_proxy):
    n = matrix.shape[0]
    m = matrix.shape[1]
    similarity_pairs = np.zeros(len(pairs))
    for i in prange(len(pairs)):
        subset1 = matrix[pairs[i][0]] #replicate_row(subset_matrix, i)  
        subset2 = matrix[pairs[i][1]]
        subset1Merch = matrixMerch[pairs[i][0]]
        subset2Merch = matrixMerch[pairs[i][1]]
        
        min_matrix = np.minimum(subset1, subset2)
        sum_min_matrix = np.sum(min_matrix, axis=-1)
        
        max_matrix = np.maximum(subset1, subset2)
        sum_max_matrix = np.sum(max_matrix, axis=-1)
        
        distMerch = 1 - np.abs(np.dot(subset1Merch, subset2Merch) / (np.linalg.norm(subset1Merch) * np.linalg.norm(subset2Merch)), 1)
        
        
        
        similarity_pairs[i] = (1 - (sum_min_matrix / sum_max_matrix)) * distMerch
        # if similarity_pairs[i] >= 1:
        #     print("similarity_pairs[i]", similarity_pairs[i])
        #     print("dist merch", distMerch, "cosine ", np.abs(np.dot(subset1Merch, subset2Merch) / (np.linalg.norm(subset1Merch) * np.linalg.norm(subset2Merch))))
        #     print("dist routes", (1 - (sum_min_matrix / sum_max_matrix)))
        #     print("prod", (1 - (sum_min_matrix / sum_max_matrix)) * distMerch)
        progress_proxy.update(1)
    return similarity_pairs

@njit(cache=True, nogil=True, parallel=True)
def compute_subset_similarity_matrix_and_merch(matrix, matrixMerch, progress_proxy):
    n = matrix.shape[0]
    n1 = matrix.shape[1]
    m = matrixMerch.shape[1]
    similarity_pairs = np.zeros((n,n))
    subset2 = matrix
    subset2Merch = matrixMerch
    squareMatrix = np.full((n, m), 2)
    routeWeights = np.full(n, 0.9)
    merchWeights = np.full(n, 0.1)
    print("n", n, "m", m)
    print("matrix merch", matrixMerch.shape)
    print("matrix square", squareMatrix.shape)
    print("routeWeights", routeWeights.shape)
    print("merchWeights", merchWeights.shape)
    normsSubset2Merch = np.sqrt(np.sum(np.power(subset2Merch, squareMatrix), axis=1))
    for i in prange(n):
        subset1 = matrix[i].reshape(1, -1) #replicate_row(subset_matrix, i)  
        subset1Merch = matrixMerch[i].reshape(1, -1)
        #print("subset1", subset1.shape)
        #print("subset2", subset2.shape)
        
        min_matrix = np.minimum(subset1, subset2)
        sum_min_matrix = np.sum(min_matrix, axis=-1)
        
        max_matrix = np.maximum(subset1, subset2)
        sum_max_matrix = np.sum(max_matrix, axis=-1)
        
        #print("sum_min_matrix", sum_min_matrix.shape)
        
        #print("merch1", subset1Merch.shape)
        #print("merch2", subset2Merch.shape)
        
        #distMerch = 1 - np.abs(np.dot(subset1Merch, subset2Merch.T) / (np.linalg.norm(subset1Merch) * np.linalg.norm(subset2Merch)))
        #distMerch = 1 - (((subset1Merch * subset2Merch).sum(axis=1) / (np.sqrt(np.sum(np.power(subset1Merch, squareMatrix),axis=1)) * normsSubset2Merch)) + 1) / 2
        
        
        min_matrix_merch = np.minimum(subset1Merch, subset2Merch)
        sum_min_matrix_merch = np.sum(min_matrix_merch, axis=-1)
        
        max_matrixMerch = np.maximum(subset1Merch, subset2Merch)
        sum_max_matrixMerch = np.sum(max_matrixMerch, axis=-1)
        distMerch = 1 - (sum_min_matrix_merch / sum_max_matrixMerch)
        
        # if i == 0 or i == n-1:
        #     print("i", i, "distMerch", distMerch.shape, distMerch)
        #     print("i", i, "sum_min_matrix", (1 - (sum_min_matrix / sum_max_matrix)).shape, (1 - (sum_min_matrix / sum_max_matrix)))
        #     print("i", i, "prod", ((1 - (sum_min_matrix / sum_max_matrix)) * distMerch).shape, ((1 - (sum_min_matrix / sum_max_matrix)) * distMerch))
        #print(i, (1 - (sum_min_matrix / sum_max_matrix)) * distMerch)
        #similarity_pairs[i] = ((1 - (sum_min_matrix / sum_max_matrix)) + distMerch)/2
        routeDistance = 1 - (sum_min_matrix / sum_max_matrix)
        similarity_pairs[i] = np.power(routeDistance, routeWeights) * np.power(distMerch, merchWeights)
        # if np.isnan(similarity_pairs[i]).any():
        #     np.set_printoptions(threshold=10000)
        #     # print("similarity_pairs[i]", similarity_pairs[i])
        #     print("dist merch", distMerch)
        #     # print("dist routes", routeDistance)
        #     # print("pow1", np.power(routeDistance, routeWeights))
        #     # print("pow2", np.power(distMerch, merchWeights))
        #     # print("prod", np.power(routeDistance, routeWeights) * np.power(distMerch, merchWeights))
        #     # print("powers", routeWeights, merchWeights)
        #     print("BROKEN")
        #     return
        #similarity_pairs[i] = (1 - (sum_min_matrix / sum_max_matrix)) * (distMerch)
        #similarity_pairs[i] = 1 - (sum_min_matrix / sum_max_matrix + distMerch) / 2
        # if similarity_pairs[i] >= 1:
        #     print("similarity_pairs[i]", similarity_pairs[i])
        #     print("dist merch", distMerch, "cosine ", np.abs(np.dot(subset1Merch, subset2Merch) / (np.linalg.norm(subset1Merch) * np.linalg.norm(subset2Merch))))
        #     print("dist routes", (1 - (sum_min_matrix / sum_max_matrix)))
        #     print("prod", (1 - (sum_min_matrix / sum_max_matrix)) * distMerch)
        progress_proxy.update(1)
    return similarity_pairs

@njit(cache=True, nogil=True, parallel=True)
def compute_subset_similarity_matrices(subset_matrix1, subset_matrix2, progress_proxy):
    n = subset_matrix1.shape[0]
    m = subset_matrix2.shape[0]
    #subset_matrix = subset_matrix.astype(np.int64)
    subset_similarity_matrix = np.zeros((n, m))
    subset2 = subset_matrix2
    for i in prange(n):
        subset1 = subset_matrix1[i].reshape(1, -1) #replicate_row(subset_matrix, i)    
        min_matrix = np.minimum(subset1, subset2)
        sum_min_matrix = np.sum(min_matrix, axis=-1)
        
        max_matrix = np.maximum(subset1, subset2)
        sum_max_matrix = np.sum(max_matrix, axis=-1)
        
        subset_similarity_matrix[i] = 1 - (np.divide(sum_min_matrix, sum_max_matrix)).T
        progress_proxy.update(1)
    return subset_similarity_matrix

def jaccard_similarity_minhash_lsh_route_merch(matrix, matrixMerch, thresh_user=0.2):
    #similarity_matrix = csr_matrix((matrix.shape[0], matrix.shape[0]), dtype=np.float64)
    #similarity_matrix = lil_matrix((matrix.shape[0], matrix.shape[0]), dtype=np.float64)
    pairs = lsh(matrix, thresh_user=thresh_user)
    #uniqueRows = np.unique([i for i, j in pairs] + [j for i, j in pairs])
    uniqueRowsSet = set([i for i, j in pairs] + [j for i, j in pairs]) # (1,2) (1,4) (1,5)
    neverSeen = set([i for i in range(matrix.shape[0])]) - uniqueRowsSet
    print("neverSeen", neverSeen)
    #print("uniqueRows numpy", len(uniqueRows))
    print("num of subset of rows to check similarity:", len(uniqueRowsSet))
    #print(" num of pairs", len(uniqueRowsSet)*(len(uniqueRowsSet)-1)/2)
    print(" num of pairs", len(pairs))
    print(" instead of", matrix.shape[0]*(matrix.shape[0]-1)/2)
    print("improved by", (1 - len(pairs) / (matrix.shape[0]*(matrix.shape[0]-1)/2)) *100, "%")
    #print("num of pairs", len(pairs))
    #print("num unique i", len(set([i for i, j in pairs])))
    #print("num unique j", len(set([j for i, j in pairs])))
    #print("num unique rows", len(uniqueRows))
    #map_i = {i: index for i, index in enumerate(uniqueRowsSet)}
    #map_i_array = np.array([map_i[i] for i in range(len(map_i))])
    
    #subset_matrix = matrix[list(uniqueRowsSet)]
    
    #subset_similarity_matrix = np.full((subset_matrix.shape[0], subset_matrix.shape[0]), np.inf)
    
    # compute connected components on pairs
    # print("Computing connected components...")
    # G = nx.Graph()
    # G.add_edges_from(pairs)
    # connected_components = nx.connected_components(G)
    # #print("num connected components", ))
    # islands = []
    # for i, cc in enumerate(connected_components):
    #     islands.append(list(cc))
        
    # islands.append(islands[0])
    
    # minimum linkage
    #pairs = np.concatenate([pairs, np.array([[i, j] for i, j in zip(islands[:-1], islands[1:])])])
    
    # complete linkage
    #pairs = np.concatenate([pairs, np.array([[i, j] for i in islands for j in islands if i != j])])
    
    # pairwise linkage with every element of islands with every other element of all the other islands
    #pairs = np.array([[i, j] for island1 in islands for island2 in islands if island1 != island2 for i in island1 for j in island2])
    
    # G = nx.Graph()
    # G.add_edges_from(pairs)
    # connected_components = nx.connected_components(G)
    # print("num connected components after", len(list(connected_components)))
    
        
    print("Computing jaccard similarity on subset matrix...")
    #print("subset matrix", subset_matrix.shape)

    # with ProgressBar(total=len(pairs)) as progress:
    #     distance_pairs = compute_subset_similarity_matrix_only_pairs(matrix, matrixMerch, pairs, progress)
    
    sortedUniqueRowsSet = sorted(list(uniqueRowsSet))
    subset_matrix = matrix[sortedUniqueRowsSet]
    subset_matrixMerch = matrixMerch[sortedUniqueRowsSet]
    print("subset_matrix", subset_matrix.shape, subset_matrix[0])
    print("subset_matrixMerch", subset_matrixMerch.shape, subset_matrixMerch[0])
    with ProgressBar(total=len(sortedUniqueRowsSet)) as progress:
        subset_sim_matrix = compute_subset_similarity_matrix_and_merch(subset_matrix, subset_matrixMerch, progress)
    print("subset_sim_matrix", subset_sim_matrix.shape, subset_sim_matrix[0])
    print("subset_sim_matrix contains nan", np.isnan(subset_sim_matrix).any())
    print("nan indices", len(np.argwhere(np.isnan(subset_sim_matrix))), np.argwhere(np.isnan(subset_sim_matrix)))
    
    # if len(neverSeen) > 0:
    #     for i, n in enumerate(neverSeen):
    #         distance_pairs = np.concatenate([distance_pairs, [1]*(matrix.shape[0]-1-i)])
        
    #     pairs = np.concatenate([pairs, np.array([[i, j] for i,n  in enumerate(neverSeen) for j in range(i, matrix.shape[0]) if i != j])])
    #print("pairs", pairs.shape, pairs[-10:])
    # map back to original matrix
    print("Mapping back to original matrix...")
    
    lenMatrixNoNeverSeen = matrix.shape[0] - len(neverSeen)
    
    # remove never seen rows and map indices
    map_indices = {}
    sortedNeverSeen = sorted(list(neverSeen))
    counter = 0
    for i in range(matrix.shape[0]):
        if i in sortedNeverSeen:
            continue
        map_indices[i] = counter
        counter += 1
        
    print("map_indices", map_indices)
    map_indices_back = {v: k for k, v in map_indices.items()}
    
    # Create data array for COO matrix
    # indices_i, indices_j = np.array(pairs).T   # 9400    
    # # map indices to new indices
    # indices_i = np.array([map_indices[i] for i in indices_i])
    # indices_j = np.array([map_indices[j] for j in indices_j])
    
    # data = np.concatenate([distance_pairs, distance_pairs])

    # # Create row and column index arrays for COO matrix
    # rows = np.concatenate([indices_i, indices_j])
    # cols = np.concatenate([indices_j, indices_i])

    # # Create COO matrix
    # similarity_matrix = coo_matrix((data, (rows, cols)), shape=(lenMatrixNoNeverSeen, lenMatrixNoNeverSeen))
    
    # indices_i, indices_j = np.triu_indices(subset_sim_matrix.shape[0], k=1)
    # print("indices_i", indices_i.shape, indices_i)
    # print("indices_j", indices_j.shape, indices_j)
    # # map indices to new indices
    # indices_i_mapped = np.array([map_indices_back[i] for i in indices_i])
    # indices_j_mapped = np.array([map_indices_back[j] for j in indices_j])
    
    # # create coo matrix
    
    # # Create data array for COO matrix
    # data = np.concatenate([subset_sim_matrix[indices_i, indices_j], subset_sim_matrix[indices_i, indices_j]])
    
    # # Create row and column index arrays for COO matrix
    # rows = np.concatenate([indices_i_mapped, indices_j_mapped])
    # cols = np.concatenate([indices_j_mapped, indices_i_mapped])
    
    # # Create COO matrix
    # similarity_matrix = coo_matrix((data, (rows, cols)), shape=(lenMatrixNoNeverSeen, lenMatrixNoNeverSeen))
    
    
    
    #similarity_matrix = similarity_matrix.tocsr()
    # Update the similarity matrix
    #similarity_matrix[map_i_array[indices_i], map_i_array[indices_j]] = subset_similarity_matrix[indices_i, indices_j]
    #similarity_matrix[map_i_array[indices_j], map_i_array[indices_i]] = subset_similarity_matrix[indices_i, indices_j]
    
    # for i, j in tqdm(pairs, desc="lsh sim"):
    #     similarity_matrix[i, j] = np.count_nonzero(matrix[i, :] == matrix[j, :]) / matrix.shape[1]
    #     similarity_matrix[j, i] = similarity_matrix[i, j]
    
    #similarity_matrix.setdiag(1)
    subset_sim_matrix = csr_matrix(subset_sim_matrix)
    
    return subset_sim_matrix, map_indices_back


# def jaccard_similarity_minhash_lsh(matrix, thresh_user=0.2):
#     #similarity_matrix = csr_matrix((matrix.shape[0], matrix.shape[0]), dtype=np.float64)
#     #similarity_matrix = lil_matrix((matrix.shape[0], matrix.shape[0]), dtype=np.float64)
#     pairs = lsh(matrix, thresh_user=thresh_user)
#     #uniqueRows = np.unique([i for i, j in pairs] + [j for i, j in pairs])
#     uniqueRowsSet = set([i for i, j in pairs] + [j for i, j in pairs]) # (1,2) (1,4) (1,5)
#     #print("uniqueRows numpy", len(uniqueRows))
#     print("num of subset of rows to check similarity:", len(uniqueRowsSet))
#     #print(" num of pairs", len(uniqueRowsSet)*(len(uniqueRowsSet)-1)/2)
#     print(" num of pairs", len(pairs))
#     print(" instead of", matrix.shape[0]*(matrix.shape[0]-1)/2)
#     print("improved by", len(pairs) / (matrix.shape[0]*(matrix.shape[0]-1)/2)*100, "%")
#     #print("num of pairs", len(pairs))
#     #print("num unique i", len(set([i for i, j in pairs])))
#     #print("num unique j", len(set([j for i, j in pairs])))
#     #print("num unique rows", len(uniqueRows))
#     map_i = {i: index for i, index in enumerate(uniqueRowsSet)}
#     map_i_array = np.array([map_i[i] for i in range(len(map_i))])
    
#     subset_matrix = matrix[list(uniqueRowsSet)]
    
#     subset_similarity_matrix = np.full((subset_matrix.shape[0], subset_matrix.shape[0]), np.inf)
    
#     print("Computing jaccard similarity on subset matrix...")
#     print("subset matrix", subset_matrix.shape)
    
#     # subset1 = subset_matrix[:, None, :]
#     # subset2 = subset_matrix[None, :, :]
#     # min_matrix = np.minimum(subset1, subset2) # (10, 100) -> (10, 1, 100) -> (1, 10, 100) -> (10, 10, 100)
#     # sum_min_matrix = np.sum(min_matrix, axis=-1)
#     # print("sum_min_matrix", sum_min_matrix.shape)
    
#     # max_matrix = np.maximum(subset1, subset2)
#     # sum_max_matrix = np.sum(max_matrix, axis=-1)
#     # print("sum_max_matrix", sum_max_matrix.shape)
    
#     #subset_similarity_matrix =  sum_min_matrix / sum_max_matrix
#     #subset_similarity_matrix = np.divide(sum_min_matrix, sum_max_matrix, out=np.zeros_like(sum_min_matrix), where=(sum_max_matrix != 0))
    
#     # for i in tqdm(range(subset_matrix.shape[0])):
#     #     subset1 = np.vstack([subset_matrix[i]] * subset_matrix.shape[0])
#     #     subset2 = subset_matrix
#     #     min_matrix = np.minimum(subset1, subset2) # (10, 100) -> (10, 1, 100) -> (1, 10, 100) -> (10, 10, 100)
#     #     sum_min_matrix = np.sum(min_matrix, axis=-1)
#     #     #print("sum_min_matrix", sum_min_matrix.shape)
        
#     #     max_matrix = np.maximum(subset1, subset2)
#     #     sum_max_matrix = np.sum(max_matrix, axis=-1)
#     #     #print("sum_max_matrix", sum_max_matrix.shape)
        
#     #     subset_similarity_matrix[i] =  (sum_min_matrix / sum_max_matrix).T
#     with ProgressBar(total=subset_matrix.shape[0]) as progress:
#         subset_similarity_matrix = compute_subset_similarity_matrix(subset_matrix, progress)
    
#     # map back to original matrix
#     print("Mapping back to original matrix...")
#     # Create arrays of indices
#     # Create data array for COO matrix
#     indices_i, indices_j = np.triu_indices(subset_similarity_matrix.shape[0], k=1)
#     data = np.concatenate([subset_similarity_matrix[indices_i, indices_j], subset_similarity_matrix[indices_i, indices_j]])

#     # Create row and column index arrays for COO matrix
#     rows = np.concatenate([map_i_array[indices_i], map_i_array[indices_j]])
#     cols = np.concatenate([map_i_array[indices_j], map_i_array[indices_i]])

#     # Create COO matrix
#     similarity_matrix = coo_matrix((data, (rows, cols)), shape=(matrix.shape[0], matrix.shape[0]))
    
#     # indices_i, indices_j = np.triu_indices(subset_similarity_matrix.shape[0], k=1)
#     # similarity_matrix = similarity_matrix.tocsr()
#     # # Update the similarity matrix
#     # similarity_matrix[map_i_array[indices_i], map_i_array[indices_j]] = subset_similarity_matrix[indices_i, indices_j]
#     # similarity_matrix[map_i_array[indices_j], map_i_array[indices_i]] = subset_similarity_matrix[indices_i, indices_j]
    
#     # for i, j in tqdm(pairs, desc="lsh sim"):
#     #     similarity_matrix[i, j] = np.count_nonzero(matrix[i, :] == matrix[j, :]) / matrix.shape[1]
#     #     similarity_matrix[j, i] = similarity_matrix[i, j]
    
#     #similarity_matrix.setdiag(1)
#     similarity_matrix = similarity_matrix.tocsr()
    
#     return similarity_matrix

def jaccard_similarity_minhash_lsh_two_matrices(matrix1, matrix2, thresh_user=0.2):
    #similarity_matrix = csr_matrix((matrix.shape[0], matrix.shape[0]), dtype=np.float64)
    #similarity_matrix = lil_matrix((matrix1.shape[0], matrix2.shape[0]), dtype=np.float64)
    pairs = lsh(matrix1, thresh_user=thresh_user)
    #uniqueRows = np.unique([i for i, j in pairs] + [j for i, j in pairs])
    uniqueRowsSet = set([i for i, j in pairs] + [j for i, j in pairs])
    #print("uniqueRows numpy", len(uniqueRows))
    print("num of subset of rows to check similarity:", len(uniqueRowsSet))
    print(" num of pairs", len(uniqueRowsSet)*(len(uniqueRowsSet)-1)/2)
    print(" instead of", matrix1.shape[0]*(matrix1.shape[0]-1)/2)
    print("improved by", (1 - len(pairs)*(len(pairs)-1)/2 / (matrix1.shape[0]*(matrix1.shape[0]-1)/2))*100, "%")
    #print("num of pairs", len(pairs))
    #print("num unique i", len(set([i for i, j in pairs])))
    #print("num unique j", len(set([j for i, j in pairs])))
    #print("num unique rows", len(uniqueRows))
    map_i = {i: index for i, index in enumerate(uniqueRowsSet)}
    map_i_array = np.array([map_i[i] for i in range(len(map_i))])
    
    subset_matrix1 = matrix1[list(uniqueRowsSet)]
    subset_matrix2 = matrix2[list(uniqueRowsSet)]
    
    subset_similarity_matrix = np.full((subset_matrix1.shape[0], subset_matrix2.shape[0]), np.inf)
    
    print("Computing jaccard similarity on subset matrix...")
    print("subset matrix", subset_matrix1.shape)

    with ProgressBar(total=subset_matrix1.shape[0]) as progress:
        subset_similarity_matrix = compute_subset_similarity_matrix(subset_matrix1, progress)
    
    # map back to original matrix
    print("Mapping back to original matrix...")
    # Create arrays of indices
    # Create data array for COO matrix
    indices_i, indices_j = np.triu_indices(subset_similarity_matrix.shape[0], k=1)
    data = np.concatenate([subset_similarity_matrix[indices_i, indices_j], subset_similarity_matrix[indices_i, indices_j]])
    
    # Create row and column index arrays for COO matrix
    rows = np.concatenate([map_i_array[indices_i], map_i_array[indices_j]])
    cols = np.concatenate([map_i_array[indices_j], map_i_array[indices_i]])
    
    # Create COO matrix
    similarity_matrix = coo_matrix((data, (rows, cols)), shape=(matrix1.shape[0], matrix2.shape[0]))
    similarity_matrix.setdiag(0)
    
    similarity_matrix = similarity_matrix.tocsr()
    
    return similarity_matrix
    

def jaccard_similarity_two_matrices(matrix1, matrix2):
    #intersection = np.dot(matrix, matrix.T)
    intersection = np.dot(matrix1, matrix2.T)
    row_sums1 = matrix1.sum(axis=1)
    row_sums2 = matrix2.sum(axis=1)
    union = row_sums1[:, None] + row_sums2 - intersection
    union = np.where(union == 0, 1, union)  # avoid division by zero
    jaccard_similarity = intersection / union
    return jaccard_similarity

def jaccard_similarity_matrix_merch(matrix):
    print("matrix", matrix.shape)
    min_matrix = np.minimum(matrix[:, None, :], matrix[None, :, :]) # (10, 100) -> (10, 1, 100) -> (1, 10, 100) -> (10, 10, 100)
    sum_min_matrix = np.sum(min_matrix, axis=-1)
    print("sum_min_matrix", sum_min_matrix.shape)
    
    max_matrix = np.maximum(matrix[:, None, :], matrix[None, :, :])
    sum_max_matrix = np.sum(max_matrix, axis=-1)
    print("sum_max_matrix", sum_max_matrix.shape)
    
    jaccard_similarity = sum_min_matrix / sum_max_matrix
    return jaccard_similarity

    # current wrong method
    # 1 2 3    1 4 7    1 2 3  6     6 6 6
    # 4 5 6    2 5 8    2 5 6  13    6 15 15
    # 7 8 9    3 6 9    3 6 9        6 15 24
    
    
    # right method
    # 1 2 3    1 2 3    1 2 3
    # 1 2 3    4 5 6    1 2 3
    # 1 2 3    7 8 9    1 2 3
    
    # 4 5 6    1 2 3    1 2 3
    # 4 5 6    4 5 6    4 5 6
    # 4 5 6    7 8 9    4 5 6
    
    # 7 8 9    1 2 3    1 2 3
    # 7 8 9    4 5 6    4 5 6
    # 7 8 9    7 8 9    7 8 9
    
    
    #                   6 6 6
    #                   6 15 15
    #                   6 15 24
    
def similarity_matrix_merch(matrix):
    if 1.0 - np.count_nonzero(matrix) / matrix.size > 0.5:
        print("merch matrix is sparse")
    matrix = csr_matrix(matrix)
    print("matrix merch shape", matrix.shape)
    simMatrix = cosine_similarity(matrix, dense_output=False)
    
    return simMatrix

def create_binary_matrix(routeSets):
    uniqueShingles = list(set(shingle for route in routeSets for shingle in route[1]))
    print("uniqueShingles", len(uniqueShingles))

    # Create a dictionary that maps each shingle to its index
    shingle_to_index = {shingle: index for index, shingle in enumerate(uniqueShingles)}
    print("shingle_to_index", len(shingle_to_index))

    binaryMatrix = np.zeros((len(routeSets), len(uniqueShingles)), dtype=int)

    for i, route in enumerate(routeSets):
        #print("i", i)
        # Get the indices of the shingles in this route
        indices = [shingle_to_index[shingle] for shingle in route[1]]
        # Use advanced indexing to set the corresponding elements in the binary matrix to 1
        binaryMatrix[i, indices] = 1

    return binaryMatrix

def create_binary_matrix_minhash(matrix):
    numUnique = np.unique(matrix)
    binaryMatrix = np.zeros((matrix.shape[0], len(numUnique)), dtype=int)
    for i, route in enumerate(matrix):
        indices = np.where(route == 1)[0]
        binaryMatrix[i, indices] = 1
    
    return binaryMatrix

def create_binary_matrices(routeSet1, routeSet2):
    # create binary matrix where each row represents a route
    uniqueShinglesBoth = list(set([shingle for route in routeSet1 for shingle in route[1]] + [shingle for route in routeSet2 for shingle in route[1]]))
    binaryMatrix1 = np.zeros((len(routeSet1), len(uniqueShinglesBoth)))
    binaryMatrix2 = np.zeros((len(routeSet2), len(uniqueShinglesBoth)))
    for i, route in enumerate(routeSet1):
        for shingle in route[1]:
            binaryMatrix1[i][uniqueShinglesBoth.index(shingle)] = 1
            
    for i, route in enumerate(routeSet2):
        for shingle in route[1]:
            binaryMatrix2[i][uniqueShinglesBoth.index(shingle)] = 1
    return binaryMatrix1, binaryMatrix2

def find_num_hashes_minhash(matrix):
    if matrix.shape[1] < 1000:
        num_hash_functions = matrix.shape[1]//10
    elif matrix.shape[1] < 10_000:
        num_hash_functions = 150
    elif matrix.shape[1] < 100_000:
        num_hash_functions = 250
    else:
        num_hash_functions = 300
    return num_hash_functions


# convert routes and merchandise to binary matrices
# binary matrix where each row represents a route
print("Creating route binary matrix...")
route_matrix, route_matrix_standard = create_binary_matrices(actualSets, standardSets)
print("\nroute_matrix actual", route_matrix.shape, route_matrix[0])
print("\nroute_matrix standard", route_matrix_standard.shape, route_matrix_standard[0])

print("Minhashing route matrix...")    
num_hash_functions = find_num_hashes_minhash(route_matrix)
route_matrix = minhash(route_matrix, num_hash_functions if num_hash_functions % 2 == 0 else num_hash_functions + 1)
print("\nroute_matrix minhash", route_matrix.shape, route_matrix[0])
# binary matrix where each row represents merchandise

print("Creating merchandise binary matrix...")
merch_matrix = np.array([s[2] for s in actualSets])

print("\nmerch_matrix", merch_matrix.shape, merch_matrix)
print("merch_matrix contains nan", np.isnan(merch_matrix).any())

# compute Jaccard similarity for each matrix
# print("Computing Jaccard similarity route matrix...")
# route_similarity = jaccard_similarity_minhash_lsh(route_matrix, thresh_user=0.4)
# #route_similarity = jaccard_similarity_matrix(route_matrix)
# print("\nroute_similarity", type(route_similarity), route_similarity.shape,route_similarity[0, 0], route_similarity[0])
# #merch_similarity = jaccard_similarity_matrix_merch(merch_matrix)
# print("Computing Jaccard similarity merchandise matrix...")
# #merch_similarity = similarity_matrix_merch(merch_matrix)
# merch_similarity_lsh = jaccard_similarity_minhash_lsh(merch_matrix, thresh_user=0.4)
# print("\nmerch_similarity", type(merch_similarity_lsh), merch_similarity_lsh.shape, merch_similarity_lsh[0])

print("Computing Jaccard similarity route matrix...")
actualSetsDistances, map_indices_back = jaccard_similarity_minhash_lsh_route_merch(route_matrix, merch_matrix, thresh_user=0.4)
#route_similarity = jaccard_similarity_matrix(route_matrix)
print("\nactualSetsDistances", type(actualSetsDistances), actualSetsDistances.shape,actualSetsDistances[0, 0], actualSetsDistances[0])
print("map indices back", map_indices_back)


# # compute final Jaccard distance
# print("Multiplying Jaccard similarities...")
# actualSetsDistances = (route_similarity.multiply(merch_similarity_lsh))
# actualSetsDistances = np.nan_to_num(actualSetsDistances, nan=0)
#actualSetsDistances = 1 - actualSetsDistances
#print("\nactualSetsDistances", actualSetsDistances.shape, actualSetsDistances[0, 0], actualSetsDistances[0])

# Essentials for Task 2

# standardToActualSetsDistances = None
# #route_matrix_standard = create_binary_matrix(standardSets)
# print("\nroute_matrix_standard", route_matrix_standard.shape, route_matrix_standard[0])
# route_matrix_standard = minhash(route_matrix_standard, num_hash_functions if num_hash_functions % 2 == 0 else num_hash_functions + 1)
# print("\nroute_matrix_standard minhash", route_matrix_standard.shape, route_matrix_standard[0])

# merch_matrix_standard = np.array([s[2] for s in standardSets])

# route_similarity_standard_to_actual = jaccard_similarity_minhash_lsh_two_matrices(route_matrix, route_matrix_standard, thresh_user=0.0)
# print("\nroute_similarity_standard_to_actual", route_similarity_standard_to_actual.shape, route_similarity_standard_to_actual[0])

# merch_similarity_lsh_standard_to_actual = jaccard_similarity_minhash_lsh_two_matrices(merch_matrix, merch_matrix_standard, thresh_user=0.0)





Creating route binary matrix...

route_matrix actual (10000, 6067) [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.

minhashing: 100%|██████████| 10000/10000 [00:00<00:00, 66906.22it/s]


route_matrix minhash (10000, 150) [ 378.   44.   56.  271.  606.  146.  934.   67.  100.   45.  761.  117.
  233.  272.  166.  258.  127.  395.  487.   62.  360.  253.  497.  117.
  177.  145.  101.  115.  516.  333.  365.   81.  185.  237.  135.  275.
   94.  115.  399.  321.  140.  325.  185.   86.  571.  108.   60.    2.
  185.  139.   90.  168.  154.  260.   95.  145.   96.   24.  380.   36.
  142.   38.  140.    5.  635.  114.  614.  428.   19.  331.  121.  573.
  171.  121.  407.  158.  178.  521.    8.    3.  109.  102.  136.  310.
 1082.  625.   58.    3.    8.  509.  520.  393.    7.  581.  280.  391.
  227.    6. 1286.  218.  410.  544.    7.  244.  204.   68.  504.  143.
  202.  382.   96.  415.  328.  412.  210.    6.  469.  283.  514.   65.
  398.   71.   25.  884.  464.   51.  138.   73.   83.   88.  701.  263.
  135.  158.   42.  391.  168. 1011.  182.   56.  134.   97.  204.  156.
  364.   61.   56.   15.  401.   29.]
Creating merchandise binary matrix...

merch_matrix

Finding candidate pairs...


100%|██████████| 10000/10000 [00:02<00:00, 4501.53it/s]


neverSeen {4096, 1, 6144, 3, 8194, 4101, 8195, 8, 8202, 2060, 15, 17, 18, 2067, 20, 2069, 22, 4113, 4115, 25, 6168, 6170, 28, 8212, 2082, 8229, 38, 4135, 6185, 6187, 6190, 4144, 49, 6193, 6194, 6198, 2104, 4154, 6204, 63, 8263, 6219, 6223, 80, 6224, 6227, 85, 6232, 8280, 6234, 96, 2145, 8290, 4196, 8292, 4198, 4200, 4202, 2156, 2163, 2164, 8308, 6264, 8319, 2176, 129, 6276, 8324, 6279, 4234, 2187, 142, 143, 6290, 147, 2197, 150, 8341, 2201, 6297, 4252, 2205, 6304, 163, 2211, 168, 6313, 2219, 6315, 2221, 174, 4270, 6318, 6322, 6324, 182, 6327, 4280, 2234, 8992, 2236, 6332, 4290, 6339, 6341, 4296, 4297, 6344, 203, 4303, 8402, 6355, 8404, 2261, 6358, 2266, 2270, 6366, 4320, 8419, 4324, 8424, 233, 2281, 6379, 2284, 4333, 2286, 2287, 8189, 6386, 8437, 8439, 248, 252, 6396, 2304, 257, 4353, 6402, 6403, 263, 4360, 6413, 2319, 2320, 6419, 279, 2327, 282, 2330, 2332, 4379, 6426, 2337, 290, 2338, 2339, 6438, 2345, 298, 299, 300, 302, 2351, 304, 305, 2352, 313, 2361, 2363, 8509, 318, 6462, 320, 6

  0%|          | 0/8910 [00:00<?, ?it/s]

n 8910 m 20
matrix merch (8910, 20)
matrix square (8910, 20)
routeWeights (8910,)
merchWeights (8910,)
subset_sim_matrix (8910, 8910) [0.         0.43462766 0.32963416 0.39401235 0.38214857 0.43454021
 0.35846186 0.39627426 0.32668512 0.37843588 0.40482983 0.44601287
 0.30249599 0.34489761 0.369971   0.45559152 0.43668556 0.43380738
 0.44851568 0.2969475  0.38412999 0.44956984 0.32229105 0.32609678
 0.37450794 0.35436132 0.37226081 0.31843538 0.18396349 0.40809542
 0.38561264 0.33284427 0.35222172 0.37856403 0.33908588 0.33662019
 0.3324536  0.34133955 0.41445999 0.3750063  0.31268535 0.43363723
 0.41107617 0.38371879 0.25815513 0.27282677 0.40820962 0.29865355
 0.38495697 0.26666633 0.31039157 0.44819643 0.30514184 0.2892339
 0.30840371 0.42000267 0.45187087 0.32628199 0.3601835  0.33899066
 0.36933343 0.3998635  0.29154068 0.43854681 0.42826914 0.44852215
 0.41279352 0.41627235 0.42566869 0.30597194 0.30016736 0.43663894
 0.42288305 0.37043245 0.35770562 0.32728151 0.39302361 0.42071

In [71]:
#np.mean(np.mean(np.abs(actualSetsDistances - test), axis=1))

In [72]:
# def jaccard_distance_routes(route1, route2):
#     id1 = route1[0]
#     id2 = route2[0]
#     r1 = set(route1[1])
#     r2 = set(route2[1])
#     merch1 = route1[2]
#     merch2 = route2[2]
    
#     intersection = len(list(r1.intersection(r2)))
#     union = (len(r1) + len(r2)) - intersection
#     jaccard_similarity = float(intersection) / union if union != 0 else 0
    
#     intersectionMerch = np.sum(np.minimum(merch1, merch2))
#     unionMerch = np.sum(np.maximum(merch1, merch2))
#     jaccard_similarity_merch = float(intersectionMerch) / unionMerch if unionMerch != 0 else 0
    
#     return 1 - (jaccard_similarity + jaccard_similarity_merch) / 2

# forward_expansion = len(actualSets) // len(standardSets)
# # precompute the distances between the elements of the actual sets
# actualSetsDistances = np.zeros((len(actualSets), len(actualSets)))
# for i in range(len(actualSets)):
#     for j in range(len(actualSets)):
#         actualSetsDistances[i,j] = jaccard_distance_routes(actualSets[i], actualSets[j])
#print("actualSetsDistances: ", actualSetsDistances.shape, actualSetsDistances[0])

In [73]:
# HDBSCAN clustering
# Compute HDBSCAN

# import gridsearchcv

#grid = GridSearchCV(hdbscan, scoring=hdbscan.probabilities_, , verbose=1)
# min_cluster_size = [10, 15, 20, 25, 30, 35, 40, 45, 50]
# max_cluster_size = [55, 60, 65, 75, 80, 85, 90, 95, 100]
forward_expansion = len(actualSets) // len(standardSets) #! TODO: change to mean
print("forward_expansion", forward_expansion)
from hdbscan import HDBSCAN as hdbsc

#actualSetsDistances = actualSetsDistances.astype(np.float64)

# find rows with only zeros and set them to 1 of csr matrix
#actualSetsDistances[actualSetsDistances.getnnz(1)==0, :] = 1
#print("get nnz", np.where((actualSetsDistances.getnnz(1)==1)==True)[0])
#print("get nnz of 2 values", (actualSetsDistances==0))
#print(actualSetsDistances[:, 9816])
#print(actualSetsDistances[9816, :])
#actualSetsDistances[:, actualSetsDistances.getnnz(1)==0] = 1

#actualSetsDistances.setdiag(0)
#actualSetsDistances = actualSetsDistances.toarray()
print("actualSetsDistances", actualSetsDistances.shape, actualSetsDistances)


print("type(actualSetsDistances)", type(actualSetsDistances), actualSetsDistances.dtype, actualSetsDistances.shape, actualSetsDistances.count_nonzero(), min(actualSetsDistances.getnnz(axis=-1)), np.unique(actualSetsDistances.data))
#actualSetsDistances = np.array(actualSetsDistances)

#print("get nnz of 2 values", np.where((actualSetsDistances==2))[0])


hdb = HDBSCAN(min_cluster_size=forward_expansion//3, max_cluster_size=forward_expansion, metric="precomputed", store_centers=None,allow_single_cluster=False, metric_params={"max_distance": 0} ).fit(actualSetsDistances.copy())
#hdb = DBSCAN(eps=0.5, min_samples=forward_expansion//3, metric="precomputed").fit(actualSetsDistances.copy())

labels_HDBSCAN = hdb.labels_
print("num clusters found: ", len(set(labels_HDBSCAN)))
print("biggest cluster: ", max(labels_HDBSCAN, key=list(labels_HDBSCAN).count), " num elements: ", list(labels_HDBSCAN).count(max(labels_HDBSCAN, key=list(labels_HDBSCAN).count)))

# Create a color map that maps each unique label to a color
unique_labels = np.unique(labels_HDBSCAN)
#unique_labels = unique_labels[unique_labels != -1]
print("unique_labels: ", len(unique_labels), unique_labels, "standard sets len", len(standardSets))

#centroids = hdb.centroids_
#medoids = hdb.medoids_

#print("centroids: ", centroids.shape)
#print("medoids: ", medoids.shape)

# find the medoids using the clusters found by HDBSCAN
print("actualSetsDistances: ", actualSetsDistances.shape, actualSetsDistances[0])
medoidsIndices = []
cluster_mean_distances = []
for cluster in unique_labels:
    #print("cluster: ", cluster)
    if cluster in [-1, -2, -3]:
        continue
    cluster_elements = np.where(labels_HDBSCAN == cluster)[0]
    #print("cluster_elements: ", cluster_elements.shape, cluster_elements)
    #print("cluster_elements: ", actualSetsDistances[cluster_elements].shape)
    cluster_distances = actualSetsDistances[cluster_elements][:,cluster_elements]
    #print("cluster_distances: ", cluster_distances.shape, cluster_distances)
    #print("real distance", actualSetsDistances[cluster_elements[0], cluster_elements[0]])
    cluster_distances_sum = np.sum(cluster_distances, axis=1)
    cluster_distances_mean = np.mean(cluster_distances, axis=1)
    cluster_mean_distances.append(np.min(cluster_distances_mean))
    #print("cluster min mean distance: ", np.min(cluster_distances_mean))
    medoid = cluster_elements[np.argmin(cluster_distances_sum)]
    #medoidMean = cluster_elements[np.argmin(cluster_distances_mean)]
    #print("medoidMean", medoidMean, "medoid", medoid)
    #print("medoid", medoid)
    medoidsIndices.append(medoid)
medoidsIndices = np.array(medoidsIndices)

print("medoidsIndices: ", medoidsIndices.shape, medoidsIndices)
print("cluster_mean_distances: ", len(cluster_mean_distances), cluster_mean_distances)


forward_expansion 1000
actualSetsDistances (8910, 8910)   (0, 1)	0.4346276628123767
  (0, 2)	0.3296341592788487
  (0, 3)	0.39401234914861416
  (0, 4)	0.382148570239762
  (0, 5)	0.4345402129698871
  (0, 6)	0.3584618563898263
  (0, 7)	0.3962742555793768
  (0, 8)	0.32668512166463914
  (0, 9)	0.3784358783346844
  (0, 10)	0.40482982636321946
  (0, 11)	0.44601287298342723
  (0, 12)	0.30249598826757096
  (0, 13)	0.3448976144160513
  (0, 14)	0.36997099816986107
  (0, 15)	0.4555915225276821
  (0, 16)	0.4366855553588897
  (0, 17)	0.4338073769438163
  (0, 18)	0.4485156790233883
  (0, 19)	0.29694749819519933
  (0, 20)	0.3841299886792443
  (0, 21)	0.44956984246401904
  (0, 22)	0.3222910468431884
  (0, 23)	0.3260967804008593
  (0, 24)	0.3745079376257376
  (0, 25)	0.35436131995076176
  :	:
  (8909, 8871)	0.3710415137716639
  (8909, 8873)	0.3594875639493601
  (8909, 8875)	0.27110905183688083
  (8909, 8877)	0.3667854685486898
  (8909, 8878)	0.2708106404130248
  (8909, 8880)	0.25352006808398025
  (8909,

In [74]:
completeSets = actualSets + standardSets
print("completeSets: ", len(completeSets))
route_matrix_with_standard = create_binary_matrix(completeSets)
# binary matrix where each row represents merchandise
merch_matrix_with_standard = np.array([s[2] for s in completeSets])

# compute Jaccard similarity for each matrix
route_similarity_with_standard = jaccard_similarity_matrix(route_matrix_with_standard)
merch_similarity_with_standard = similarity_matrix_merch(merch_matrix_with_standard).toarray()
print("route_similarity_with_standard", route_similarity_with_standard.shape, route_similarity_with_standard[0])
print("merch_similarity_with_standard", merch_similarity_with_standard.shape, merch_similarity_with_standard[0])
completeSetsDistances = np.multiply(route_similarity_with_standard, merch_similarity_with_standard)
print("completeSetsDistances", type(completeSetsDistances), completeSetsDistances.shape, completeSetsDistances[0])
completeSetsDistances = np.nan_to_num(completeSetsDistances, nan=0)
completeSetsDistances = 1 - completeSetsDistances
completeSetsDistances = np.array(completeSetsDistances)
print("completeSetsDistances", completeSetsDistances.shape, completeSetsDistances[0])

perplexity = 50 if len(completeSetsDistances) > 50 else len(completeSetsDistances) - 1
completeSetTSNE = TSNE(n_components=3, perplexity=perplexity, n_iter=1000, verbose=1).fit_transform(completeSetsDistances)

completeSets:  10010
uniqueShingles 6067
shingle_to_index 6067
matrix jaccard is sparse
intersection (10010, 10010) <class 'numpy.matrix'>
row_sums (10010,)
union (10010, 10010)
union (10010, 10010)
jaccard_similarity (10010, 10010) <class 'numpy.matrix'>
jaccard_similarity contains nan False
matrix merch shape (10010, 20)
route_similarity_with_standard (10010, 10010) [[1.         0.21052632 0.36363636 ... 0.         0.         0.        ]]
merch_similarity_with_standard (10010, 10010) [1.         0.9865857  0.98932837 ... 0.96588801 0.89446583 0.95152419]
completeSetsDistances <class 'numpy.matrix'> (10010, 10010) [[1.         0.20770225 0.35975577 ... 0.         0.         0.        ]]
completeSetsDistances (10010, 10010) [4.44089210e-16 7.92297746e-01 6.40244228e-01 ... 1.00000000e+00
 1.00000000e+00 1.00000000e+00]
[t-SNE] Computing 151 nearest neighbors...
[t-SNE] Indexed 10010 samples in 0.019s...
[t-SNE] Computed neighbors for 10010 samples in 8.104s...
[t-SNE] Computed conditio

In [75]:


# reorder the labels to have colors matching the cluster results, using medoids which are closer to the standard vectors
medoidSets = [actualSets[i] for i in medoidsIndices]
print("medoidSets: ", len(medoidSets))

num_clusters_unique = unique_labels[unique_labels >= 0]
#print("num_clusters_unique: ", len(num_clusters_unique), num_clusters_unique)

assert len(medoidSets) == len(num_clusters_unique), "The number of medoids is not equal to the number of unique labels"   

if len(medoidSets) == 0:
    print("No clustroids found")
else:

    route_matrix_standard, route_matrix_medoids = create_binary_matrices(standardSets, medoidSets)

    simMatrixMixed = jaccard_similarity_two_matrices(route_matrix_medoids, route_matrix_standard)

    #print("route_matrix_standard: ", route_matrix_standard.shape)

    #print("route_matrix_actual: ", route_matrix_medoids.shape)

    #print("simMatrixMixed: ", simMatrixMixed.shape, simMatrixMixed[0])


    CAN_BE_ORDERED = False
    # get the closest standard vector for each medoid using simMatrixMixed

    argmax = np.argmax(simMatrixMixed, axis=1) # get the index of the closest standard vector for each medoid
    print("argmax: ", argmax.shape, argmax)

    if len(set(argmax)) == len(medoidsIndices): # if the argmax are all different, then the medoids can be reordered
        print("argmax is correct, can be reordered")
        CAN_BE_ORDERED = True
        # reorder medoidsIndices
        #print("argmax: ", argmax.shape, argmax)
        #print("medoidsIndices: ", medoidsIndices.shape, medoidsIndices)
        
        
        # Create an array of zeros with the same shape as the original array
        # result = np.zeros_like(medoidsIndices)
        # argsort = np.argsort(argmax)
        # print("argsort: ", argsort.shape, argsort)
        # # Fill the result array using the permutation indices
        # result[argsort] = medoidsIndices
        # medoidsIndicesReordered = result # reorder medoidsIndices
        # result = np.zeros_like(medoidsIndices)
        # unique_labels_filtered = unique_labels[unique_labels >= 0]
        # result[argsort] = unique_labels_filtered
        unique_labels_reordered = argmax   # 4, 2, 5, 10, ... -> 10, 4, 5, 2, ...
        
        #medoidsIndicesReordered = medoidsIndices[argmax] # reorder medoidsIndices
        #print("medoidsIndices: ", medoidsIndicesReordered.shape, medoidsIndicesReordered)
        #unique_labels = unique_labels[argmax]


    # for i in range(len(standardSets)):
    #     #distances = np.linalg.norm(medoids - standardVectors[i], axis=1)
    #     distancesCosine = []
    #     for j in range(len(medoidsIndices)):
    #         distancesCosine.append(cosine(actualSets[j], standardSets[i]))
    #     closest_medoid = np.argmin(distancesCosine)
        
    #     if closest_medoid not in unique_labels_reordered:
    #         unique_labels_reordered.append(closest_medoid)
    #     else:
    #         print("closest_medoid already in unique_labels_reordered")
    #         can_be_reordered = False
    #         break

    if not CAN_BE_ORDERED:
        #unique_labels_reordered = unique_labels

        #unique_labels = unique_labels_reordered
        #unique_labels = np.unique(labels_HDBSCAN)
        
        print("unique_labels: ", len(unique_labels), unique_labels)
    else:
        print("unique_labels_reordered: ", len(unique_labels_reordered), unique_labels_reordered)
        #unique_labels = unique_labels_reordered
        # compare if distances between clustroids and standard vectors are smaller than distances between standard vectors and other actual vectors

        #distancesClustroids = simMatrixMixed[np.arange(len(simMatrixMixed)), argmax]
        
    distancesClustroids = []
    distancesStandardVectors = []
    distancesStandardVectors2 = []
    # for i, clustroid in enumerate(medoidsIndices):
    #     distMedCluster = completeSetsDistances[:len(actualSets), :len(actualSets)][clustroid, labels_HDBSCAN == i]
    #     #print(labels_HDBSCAN)
    #     #print(labels_HDBSCAN == argmax[i])
    #     print("distMedCluster: ", np.sum(distMedCluster), len(distMedCluster), distMedCluster)
    #     # make distMedCluster a single list, no np.sum since they are inhomogeneous lists
    #     #print()
    #     #print(actualRefStandardIds)
    #     distStdCluster = completeSetsDistances[len(actualSets):, :len(actualSets)][i, np.where(np.array(actualRefStandardIds) == i)[0]]
    #     print("distStdCluster: ", np.sum(distStdCluster), len(distStdCluster), distStdCluster)
        
    #     distancesClustroids.append(np.mean(distMedCluster))
    #     distancesStandardVectors2.append(np.mean(distStdCluster))
    actualRefStandardIdsNumpy = np.array(actualRefStandardIds)
    for i, stdID in enumerate(standardRefIds):
        distStdCluster = completeSetsDistances[len(actualSets):, :len(actualSets)][i, np.where(actualRefStandardIdsNumpy == stdID)[0]]
        #print("distStdCluster: ", np.mean(distStdCluster), len(distStdCluster), distStdCluster)
        distancesStandardVectors.append(np.mean(distStdCluster))
    
    mean_distance_clustroids = np.mean(cluster_mean_distances)
    std_dev_distance_clustroids = np.std(cluster_mean_distances)

    mean_distance_standard_vectors = np.mean(distancesStandardVectors)
    std_dev_distance_standard_vectors = np.std(distancesStandardVectors)

    cv_clustroids = std_dev_distance_clustroids / mean_distance_clustroids
    cv_standard_vectors = std_dev_distance_standard_vectors / mean_distance_standard_vectors
    # print in green if the improvement is positive, in red if it is negative
    print("\n\033[94mMean distance from vectors of the same cluster to:")
    print("         clustroids: ", mean_distance_clustroids)
    #print("         first     : ", np.mean(distancesClustroids))
    print("   standard vectors: ", mean_distance_standard_vectors)
    #print("first                ", np.mean(distancesStandardVectors2))
    

    print("\nStd dev distance from vectors of the same cluster to:")
    print("         clustroids: ", std_dev_distance_clustroids)
    print("   standard vectors: ", std_dev_distance_standard_vectors)

    print("\nCoefficient of variation from vectors of the same cluster to:")
    print("         clustroids: ", cv_clustroids)
    print("   standard vectors: ", cv_standard_vectors)
    print("\033[0m")

    #ratio = np.mean(distancesClustroids) / np.mean(distancesStandardVectors)
    ratio = mean_distance_clustroids / mean_distance_standard_vectors
    percentage = (1 - ratio) * 100

    print("\033[93mMean:\033[0m")
    if percentage > 0:
        # print in green if the improvement is positive, in red if it is negative
        print("   Improvement: \033[92m{:.2f}% \033[0m".format(percentage))
    else:
        print("   Decline: \033[91m{:.2f}% \033[0m".format(-percentage))
        
    
    ratio = std_dev_distance_clustroids / std_dev_distance_standard_vectors
    percentage = (1 - ratio) * 100
    print("\033[93m\nStd dev:\033[0m")
    if percentage > 0:
        # print in green if the improvement is positive, in red if it is negative
        print("   Improvement: \033[92m{:.2f}% \033[0m".format(percentage))
    else:
        print("   Decline: \033[91m{:.2f}% \033[0m".format(-percentage))
        
    ratio = cv_clustroids / cv_standard_vectors
    percentage = (1 - ratio) * 100
    print("\033[93m\nTotal\033[0m")
    if percentage > 0:
        # print in green if the improvement is positive, in red if it is negative
        print("   Improvement: \033[92m{:.2f}% \033[0m".format(percentage))
    else:
        print("   Decline: \033[91m{:.2f}% \033[0m".format(-percentage))
    
    



# orderedClustroids = np.zeros_like(actualSetsDistances[medoidsIndices].copy())
# order = []
# for i, clustroid in enumerate(medoidsIndices):
#     distances = []
#     for j, standardVector in enumerate(standardSets):
#         distances.append(cosine(clustroid, standardVector))
        
#     distances = np.array(distances)
#     orderedClustroids[np.argmin(distances)] = clustroid
#     order.append(np.argmin(distances))
    
# print("order: ", order)

# if len(set(order)) == len(clustroids):
#     print("order is correct")
#     CAN_BE_ORDERED = True
#     clustroids = orderedClustroids
#     print("clustroids: ", clustroids.shape)
#     # reorder clustroidsIndices
#     clustroidsIndices = np.array(clustroidsIndices)[order]


#     # compare if distances between clustroids and standard vectors are smaller than distances between standard vectors and other standard vectors

#     distancesClustroids = []
#     distancesStandardVectors = []
#     for i, clustroid in enumerate(clustroids):
#         distancesClustroids.append(np.sum([cosine(clustroid, v) for v in actualClusters[i]]))
#         distancesStandardVectors.append(np.sum([cosine(standardVectors[i], v) for v in actualClusters[i]]))
        
#     print("distancesClustroids: ", distancesClustroids)
#     print("distancesStandardVectors: ", distancesStandardVectors)

#     print("\nMean distance from vectors of the same cluster to:")
#     print("         clustroids: ", np.mean(distancesClustroids))
#     print("   standard vectors: ", np.mean(distancesStandardVectors))

#     print("\nStd dev distance from vectors of the same cluster to:")
#     print("         clustroids: ", np.std(distancesClustroids))
#     print("   standard vectors: ", np.std(distancesStandardVectors))

#     print("\n improvement: ", 1 - np.mean(distancesClustroids) / np.mean(distancesStandardVectors), "\n")
# else:
#     print("NO ORDER IS POSSIBLE")
#     CAN_BE_ORDERED = False





medoidSets:  9
argmax:  (9,) [7 0 2 4 5 1 6 3 8]
argmax is correct, can be reordered
unique_labels_reordered:  9 [7 0 2 4 5 1 6 3 8]

Mean distance from vectors of the same cluster to:
         clustroids:  0.2231933875210741
   standard vectors:  0.31113240397360925

Std dev distance from vectors of the same cluster to:
         clustroids:  0.08757710053992743
   standard vectors:  0.03507564168737402

Coefficient of variation from vectors of the same cluster to:
         clustroids:  0.3923821467679383
   standard vectors:  0.11273541823161948

Mean:
   Improvement: 28.26% 

Std dev:
   Decline: 149.68% 

Total
   Decline: 248.06% 


In [76]:
max_len = max(len(standardSets), len(num_clusters_unique))
colors = plt.cm.jet(np.linspace(0, 1, max_len))
# print("colors", colors.shape, colors)

# print("medoid labels", [labels_HDBSCAN[i] for i in medoidsIndices])
# print("argmax", argmax)

if len(medoidSets) > 0 and CAN_BE_ORDERED:
    print("medoids added to plots and reordered")
    color_map = dict(zip(range(max_len), colors[unique_labels_reordered]))
    #rint("color_map", color_map)
else:
    color_map = dict(zip(range(max_len), colors))   # 0=red, 1=blue, 2=green, 3=yellow, 4=purple, 5=lightblue, 6=lightgreen, 7=lightyellow, 8=lightpurple
    
marker_colors = [color_map[label] if label > -1 else np.array([0,0,0,1]) for label in labels_HDBSCAN]
marker_colors_medoids = [color_map[label] if label > -1 else np.array([0,0,0,1]) for label in labels_HDBSCAN[medoidsIndices]]
#marker_colors_medoids = [color_map[label] if label > -1 else np.array([0,0,0,1]) for label in unique_labels]


# Create a trace for each type (centroids data)
traceStandard = go.Scatter3d(
    x=completeSetTSNE[len(actualSets):,0],
    y=completeSetTSNE[len(actualSets):,1],
    z=completeSetTSNE[len(actualSets):,2],
    mode='markers',
    marker=dict(
        size=7,
        color=colors,                # set color to an array/list of desired values
        opacity=1,
        symbol='diamond'
    )
)

if len(medoidSets) > 0:
    medoidsElements = completeSetTSNE[medoidsIndices] # medoidsIndices = [921, 123]
    traceMedoids = go.Scatter3d(
        x=medoidsElements[:,0],
        y=medoidsElements[:,1],
        z=medoidsElements[:,2],
        mode='markers',
        marker=dict(
            size=7,
            color=marker_colors_medoids,                # set color to an array/list of desired values
            opacity=1,
            symbol='cross'
        )
    )

# Create a trace for each type (centroids data)
traceActual = go.Scatter3d(
    x=completeSetTSNE[:len(actualSets),0],
    y=completeSetTSNE[:len(actualSets),1],
    z=completeSetTSNE[:len(actualSets),2],
    mode='markers',
    marker=dict(
        size=7,
        color=marker_colors,                # set color to an array/list of desired values
        opacity=0.1,
        symbol='circle'
    )
)

# Plot
if len(medoidSets) > 0:
    data = [traceStandard, traceActual, traceMedoids]
else:
    data = [traceStandard, traceActual]

layout = go.Layout(
    margin=dict(
        l=0,
        r=0,
        b=0,
        t=0
    )
)

fig = go.Figure(data=data, layout=layout)
fig.show()

medoids added to plots and reordered


## Ground Truth

In [77]:

colors_true = plt.cm.jet(np.linspace(0, 1, len(standardSets)))
color_map_true = dict(zip(range(max_len), colors))   # 0=red, 1=blue, 2=green, 3=yellow, 4=purple, 5=lightblue, 6=lightgreen, 7=lightyellow, 8=lightpurple
# marker colors for each point with the same color as the cluster it belongs to in the original data
marker_colors_true = [color_map_true[label] for label in actualRefStandardIds]


# Create a trace for each type (centroids data)
traceStandard_true = go.Scatter3d(
    x=completeSetTSNE[len(actualSets):,0],
    y=completeSetTSNE[len(actualSets):,1],
    z=completeSetTSNE[len(actualSets):,2],
    mode='markers',
    marker=dict(
        size=7,
        color=colors_true,                # set color to an array/list of desired values
        opacity=1,
        symbol='diamond'
    )
)

# Create a trace for each type (centroids data)
traceActual_true = go.Scatter3d(
    x=completeSetTSNE[:len(actualSets),0],
    y=completeSetTSNE[:len(actualSets),1],
    z=completeSetTSNE[:len(actualSets),2],
    mode='markers',
    marker=dict(
        size=7,
        color=marker_colors_true,                # set color to an array/list of desired values
        opacity=0.1,
        symbol='circle'
    )
)

# Plot
data = [traceStandard_true, traceActual_true]

layout = go.Layout(
    margin=dict(
        l=0,
        r=0,
        b=0,
        t=0
    )
)

fig = go.Figure(data=data, layout=layout)
fig.show()

## Output recommended standard routes

In [78]:
# Save the medoids to a file
with open(os.path.join("results", 'recStandard.json'), 'w', encoding="utf-8") as f:
    recStandard = []
    for i, index in enumerate(medoidsIndices):
        recRoute = {"id": "s" + str(i)}
        recRoute["route"] = dfActual.iloc[actualSets[index][0]]["route"]
        recStandard.append(recRoute)
    json.dump(recStandard, f, ensure_ascii=False, indent=2)

## t-SNE of centroids of clusters and actual routes

## t-SNE of clustroids, standard, and actual routes